In [1]:
# necessary packages #

#using Pkg
#Pkg.add("Distances")
using Distributions
using Random
using Distances
using LinearAlgebra
using SparseArrays
using IterativeSolvers
using ProgressMeter
using JLD2
using DataFrames

In [2]:
include("../../../util2.j")

colnorm (generic function with 1 method)

In [3]:
# unnecessary packages #

#using Pkg
#Pkg.add("UnicodePlots")
using UnicodePlots   # check the structure of the sparse matrix
using BenchmarkTools

using StatsPlots
using MCMCChains
using PrettyTables

In [4]:
Sys.free_memory()/(2^20*1024)

17.576568603515625

In [5]:
#using Pkg
#Pkg.add("ProgressMeter");

In [6]:
@time @load "../../data/LMC_data/Factor_LMC_data_expanded.jld";

  2.744790 seconds (6.87 M allocations: 788.422 MiB, 17.22% gc time)


In [7]:
using RData
@time data_cleaned = load("../../data/rawdata/data_cleaned_small_expanded.RData", convert = true)["data_cleaned_small"];
@time hold_index_set = load("../../data/rawdata/hold_index_small_expanded.RData", convert = true)

  9.911916 seconds (33.27 M allocations: 2.083 GiB, 11.85% gc time)
  0.069007 seconds (49.88 k allocations: 7.060 MiB)


Dict{String,Any} with 11 entries:
  "hold_ind4"       => Int32[796395, 815927, 678460, 506073, 78700, 980165, 206…
  "hold_ind10"      => Int32[665387, 373156, 724373, 1019331, 888091, 918487, 8…
  "hold_ind2"       => Int32[518549, 906271, 597282, 651904, 872494, 353593, 32…
  "hold_ind6"       => Int32[896510, 543595, 201130, 86952, 630506, 206437, 452…
  "hold_ind5"       => Int32[811779, 351188, 843347, 549899, 712081, 81044, 972…
  "hold_ind9"       => Int32[498700, 871568, 343872, 751268, 699631, 503105, 87…
  "hold_ind7"       => Int32[914319, 272494, 251816, 456856, 273822, 586315, 96…
  "hold_ind3"       => Int32[466194, 761309, 456463, 45604, 728959, 693334, 733…
  "hold_ind1"       => Int32[548676, 452737, 124413, 436523, 856018, 666931, 25…
  "hold_ind8"       => Int32[363116, 896446, 832503, 10248, 932012, 542066, 851…
  "hold_area_indx2" => Int32[431753, 431754, 431755, 431756, 431757, 431758, 43…

In [8]:
# pick response NDVI and EVI
# pick explanatory variables 12 to 24, no 16
DataFrames.describe(data_cleaned)

28×8 DataFrame. Omitted printing of 5 columns
│ Row │ variable                        │ mean       │ min         │
│     │ Symbol                          │ Float64    │ Float64     │
├─────┼─────────────────────────────────┼────────────┼─────────────┤
│ 1   │ x                               │ -1.04265e7 │ -1.11193e7  │
│ 2   │ y                               │ 3.83786e6  │ 3.33608e6   │
│ 3   │ scaled_x                        │ 0.6928     │ 0.0         │
│ 4   │ scaled_y                        │ 0.501779   │ 0.0         │
│ 5   │ NDVI                            │ 0.240122   │ -0.00954541 │
│ 6   │ EVI                             │ 0.150172   │ -0.00400802 │
│ 7   │ red_reflectance                 │ 0.144424   │ 0.0047      │
│ 8   │ NIR_reflectance                 │ 0.243485   │ 0.0116      │
│ 9   │ blue_reflectance                │ 0.0752273  │ 0.0001      │
│ 10  │ MIR_reflectance                 │ 0.224949   │ 0.0016      │
⋮
│ 18  │ ET                              │ 1.33848    │ -0.798508   │
│ 19  │ PLE                             │ 1.71033    │ 1.077       │
│ 20  │ PET                             │ 5.5655     │ 3.5         │
│ 21  │ LC_Type4                        │ 3.16579    │ 1.0         │
│ 22  │ Evergreen_Needleleaf_Vegetation │ 0.56063    │ 0.0         │
│ 23  │ Evergreen_Broadleaf_Vegetation  │ 0.00825588 │ 0.0         │
│ 24  │ Deciduous_Needleleaf_Vegetation │ 0.0        │ 0.0         │
│ 25  │ Deciduous_Broadleaf_Vegetation  │ 0.0295039  │ 0.0         │
│ 26  │ Annual_Broadleaf_Vegetation     │ 0.0265127  │ 0.0         │
│ 27  │ Annual_Grass_Vegetation         │ 0.290666   │ 0.0         │
│ 28  │ Non_Vegetated_or_Builtup_Lands  │ 0.0844314  │ 0.0         │

In [9]:
Y_ord = convert(Matrix, data_cleaned[:, [:NDVI, :EVI, :GPP, :PsnNet,
            :red_reflectance, :blue_reflectance , :LE, :ET, :PLE, :PET]]);
X_ord = dropzeros(sparse([fill(1.0, (N, 1)) convert(Matrix, data_cleaned[:, 28:28])]));

In [10]:
N

1020000

In [11]:
# priors #
K = 2; p = size(X_ord)[2]; q = size(Y_ord)[2];
μβ = fill(0.0, p, q); inv_Vr = spzeros(p, p);
μΛ = fill(0.0, K, q); inv_VΛ = spzeros(K, K);
aΣ = 2; bΣ = fill(1.0, q);
inv_Lr =  spzeros(p, p); Lμβ = inv_Lr * μβ;
inv_LΛ =  spzeros(K, K); LμΛ = inv_LΛ * μΛ;
aϕ = fill(200.0, K); bϕ = [8.0/200.0, 3.0 / 200.0];

In [12]:
# Some data preparations #
obs_ind = vcat([S_ind[i] .+ (i - 1) * N for i in 1:q]...)     # index of the observed location for all response among N locations
perm_ind = sortperm(vcat([S_ind[i] for i in 1:q]...))
index_S = zeros(N);                                           # build index indicating which response are observed
index_S_M = fill(0.0, N, q);
for i in 1:q
    index_S_M[S_ind[i], i] .= 1;
    index_S = index_S + 2^(i - 1) * index_S_M[:, i]
end
M_Sind = [findall(x -> x == 0.0, index_S_M[S_indx, i]) for i in 1:q];
                                                              # index of M1 among S 
dim_invD = sum(index_S_M);
invD_yind = 1:dim_invD; invD_xind = 1:dim_invD;
Xtilde_indy_up = vcat([S_indx .+ (ind - 1) * N for ind in 1:K]...);
nsam = length(perm_ind) + (K * n);

In [13]:
# preallocation #
F_sam = Array{Float64,2}(undef, n , K);
μ_m = [Array{Float64, 2}(undef, length(U_ind[i]), q) for i in 1:q];
nIndx = length(NN.nnIndx);
A = [Array{Float64}(undef, nIndx) for i in 1:K];
D = [Array{Float64}(undef, n) for i in 1:K];
I_A = [spzeros(n, n) for i in 1:K];
A_new = [Array{Float64}(undef, nIndx) for i in 1:K];
D_new = [Array{Float64}(undef, n) for i in 1:K];
I_A_new = [spzeros(n, n) for i in 1:K];
Ystar = vcat(Y_ord[S_indx, :], inv_Lr * μβ, inv_LΛ * μΛ);             # will be updated after imputing missing response
Xstar = vcat([X_ord[S_indx, :] spzeros(n, K)], [inv_Lr spzeros(p, K)], 
    [spzeros(K, p) inv_LΛ]);      
bstar = fill(0.0, q); astar = aΣ + 0.5 * n;
μγstar = vcat(μβ, μΛ); invVγstar = fill(0.0, p + K, p + K);
Y_Xm = spzeros(n + p + K, q);
Ytilde =  Array{Float64}(undef, nsam);
Xtilde = SparseMatrixCSC{Float64,Int64};
precond_D = Array{Float64, 1}(undef, K * n);
Atilde = Array{Float64}(undef, NM * m); Dtilde = Array{Float64}(undef, NM);
lll = fill(1.0, (n, 1)); lllM = fill(1.0, (NM, 1));

MCMC sampling algorithm
Q1: priors for $\nu_i$ 
Q2: $\phi_i$ may not be consistant, since the order can change 

In [14]:
Sys.free_memory()/(2^20*1024)

16.449142456054688

In [15]:
# Preallocation for MCMC samples and Initalization #
N_sam = 10000;
N_pre_burn = Integer(trunc(0.75 * N_sam));
N_pre_adapt = Integer(trunc(0.25 * N_sam));
N_after_burn = N_sam - N_pre_burn;
ω_incp_sam = Array{Float32, 2}(undef, n, q);
F_M_sam = Array{Float32, 2}(undef, NM, K);
ω_incp_M_sam = Array{Float32, 2}(undef, NM, q);
Y_M_sam = Array{Float32, 2}(undef, NM, q);

ω_incp_sam_mean = fill(0.0, n, q);
ω_incp_sam_var = fill(0.0, n, q);
Y_m_sam_mean = [fill(0.0, length(M_Sind[i])) for i in 1:length(M_Sind)];
Y_m_sam_var = [fill(0.0, length(M_Sind[i])) for i in 1:length(M_Sind)];
ω_incp_M_sam_mean = fill(0.0, NM, q);
ω_incp_M_sam_var = fill(0.0, NM, q);
Y_M_sam_mean = fill(0.0, NM, q);
Y_M_sam_var = fill(0.0, NM, q);

F_sam = Array{Float64, 2}(undef, n, K);
Y_m_sam =  [Array{Float64, 1}(undef, length(M_Sind[i])) for i in 1:q]; # misalignments
A_sam = Array{Float64, 2}(undef, N_sam, K); # acceptance rate
lh_old = 1; lh_new = 1;     # record the likelihood for updating ranges

ϕ_sam = Array{Float64, 2}(undef, K, N_sam + 1);


γ_sam = vcat(fill(0.0, p, q), 
    [0.001 0.001 0.001 0.001 0.001 0.001 0.001 1.0 0.0 0.0
     0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 0.001]);
resdiual_pre = (Y_ord - X_ord * ((X_ord'X_ord)\(X_ord'Y_ord)));
Σ_sam = fill(0.1, q);#[var(resdiual_pre[:, i]) for i in 1:q];
ω_cov_sam = fill(0.0, q, q);
ϕ_sam[:, 1] = [8.0, 3.0];# 30.0, 15.0, 20.0, 25.0];

RWM_scale = [0.1, 0.1];#, 0.3, 0.4, 0.5];                                              # random-walk metropolis step size scale 
# 0.25, 1.0
# 0.1 0.5: 0.1 0.15
# 0.3 0.8: 0.024681346078268614 0.05

In [16]:
using DelimitedFiles
writedlm("../../results/BSLMC_Factor/γ_sam_nopredC.csv", vcat(fill(0.0, 1, q), γ_sam), ", ");
writedlm("../../results/BSLMC_Factor/Σ_sam_nopredC.csv", vcat(0.0, Σ_sam), ", ");
writedlm("../../results/BSLMC_Factor/ω_cov_sam_nopredC.csv", [fill(0.0, q)], ", ");
writedlm("../../results/BSLMC_Factor/ϕ_sam_nopredC.csv", vcat(0.0, ϕ_sam[:, 1]), ", ");
writedlm("../../results/BSLMC_Factor/A_sam_nopredC.csv", 0.0, ", ");

In [17]:
Sys.free_memory()/(2^20*1024)

16.18851089477539

In [18]:
data_cleaned = nothing; hold_index_set = nothing; GC.gc();

In [19]:
Sys.free_memory()/(2^20*1024)

16.43610382080078

In [20]:
# for loop for MCMC chain #
Random.seed!(1);
prog = Progress(N_sam, 1, "Computing initial pass...", 50)
for l in 1:N_sam
    # Build the matrix D_Sigma_o^{1/2} #
    inv_sqrt_Σ_diag = 1 ./ (sqrt.(Σ_sam));
    invD_ele = [x for ind in 1:q for x in fill(inv_sqrt_Σ_diag[ind], length(S_ind[ind]))];
    invD = sparse(invD_xind, invD_yind, invD_ele); 
                        
    # Build the matrix for the first iteration #
    if l == 1
@time   for k in 1:K
            getAD(coords, NN.nnIndx, NN.nnDist, NN.nnIndxLU, ϕ_sam[k, l], 0.5, A[k], D[k]);
            I_A[k] = sparse(nnIndx_row, nnIndx_col, vcat(-A[k], ones(n)));
        end
    end         
    # Build Ytilde Xtilde
    Ytilde = vcat(invD * vcat([Y_ord[S_ind[ind], ind] - X_ord[S_ind[ind], :] * γ_sam[1:p, ind] 
                                for ind in 1:q]...), zeros(K * n));
@time    Xtilde = vcat(invD * kron(sparse(transpose(γ_sam[(p + 1):(p + K), :])), 
                            sparse(1:N, 1:N, ones(N)))[obs_ind, Xtilde_indy_up],
             blockdiag([Diagonal(1 ./ sqrt.(D[ind])) * I_A[ind] for ind in 1:K]...));
    
    # use LSMR to generate sample of F #       
#    Precond_D = colnorm(Xtilde);
#@time    F_sam = reshape(Diagonal(1 ./ Precond_D) * lsmr(Xtilde * Diagonal(1 ./ Precond_D), 
#            collect(Ytilde) + rand(Normal(), nsam)), :, K);
@time    F_sam = reshape(lsmr(Xtilde, collect(Ytilde) + rand(Normal(), nsam)), :, K);
                
    Xstar[1:n, (p + 1):(p + K)] = F_sam;        # update matrix Xstar with F
    if(l > N_pre_burn) # only save ω_incp_sam after burn-in
        ω_incp_sam = F_sam * γ_sam[(p + 1):(p + K), :] + lll * transpose(γ_sam[1, :]); 
        ω_incp_sam_mean = ω_incp_sam_mean + (ω_incp_sam ./ N_after_burn);
        ω_incp_sam_var = ω_incp_sam_var + ((ω_incp_sam.^2) ./ N_after_burn);  
        ω_cov_sam = cov(ω_incp_sam);
    else
        ω_cov_sam = cov(F_sam * γ_sam[(p + 1):(p + K), :]);
    end
    io1 = open("../../results/BSLMC_Factor/ω_cov_sam_nopredC.csv", "a" ); # covariance of latent process
    writedlm(io1, ω_cov_sam, ", ");
    close(io1); 
    
    # impute missing response  over S#
    for ind in 1:q
        #mul!(μ_m[ind], Xstar[M_Sind[ind], :], γ_sam[:, :, l]); #Xstar[M_Sind[ind], :] * γ_sam[:, ind, l]
        Y_m_sam[ind] = Xstar[M_Sind[ind], :] * γ_sam[:, ind] +    # μ_m[ind][:, ind] + 
            rand(Normal(0.0, sqrt(Σ_sam[ind])), length(M_Sind[ind]));
         
    end

    if (l > N_pre_burn)  # only save imputed Y after burn-in
        for ind in 1:q
            Y_m_sam_mean[ind] = Y_m_sam_mean[ind] + (Y_m_sam[ind] ./ N_after_burn);
            Y_m_sam_var[ind] = Y_m_sam_var[ind] + ((Y_m_sam[ind].^2) ./ N_after_burn);
        end
    end
                        
    # use MNIW to sample γ Σ #
    for ind in 1:q
        Ystar[M_Sind[ind], ind] = Y_m_sam[ind]   # update Ystar with imputed response
    end
                        
    invVγstar = cholesky(Xstar'Xstar);
    mul!(μγstar, transpose(Xstar), Ystar); μγstar = invVγstar.U \ (invVγstar.L \ μγstar);
    Y_Xm = Ystar - Xstar * μγstar;      # maybe improve?
    bstar = [bΣ[ind] + 0.5 * (norm(Y_Xm[:, ind])^2) for ind in 1:q];
    Σ_sam = [rand(InverseGamma(astar, bstar[ind]), 1)[1] for ind in 1:q];          # sample Σ
    γ_sam = (invVγstar.U \ reshape(rand(Normal(), (p + K) * q), (p + K), q)) * 
                    Diagonal(sqrt.(Σ_sam)) + μγstar;          # sample γ  
    io2 = open("../../results/BSLMC_Factor/Σ_sam_nopredC.csv", "a" );
    writedlm(io2, Σ_sam, ", ");
    close(io2); 
    io3 = open("../../results/BSLMC_Factor/γ_sam_nopredC.csv", "a" );
    writedlm(io3, γ_sam, ", ");
    close(io3)   
    
    # use metropolis-hasting to update range
    if l > 3 && l < N_pre_adapt
        RWM_scale = [sqrt(2.38^2 * var(ϕ_sam[i, Integer(floor(l / 2)):l], 
                                corrected=true) * 0.95^2 + 0.05^2 * 0.1^2) for i in 1:K];
    end
    ϕ_sam[:, l + 1] = [ϕ_sam[i, l] + RWM_scale[i] * rand(Normal(), 1)[1] for i in 1:K]; # propose next sample point
    
@time for i in 1:K
        if ϕ_sam[i, l + 1] > 0.0
            lh_old = -0.5 * (sum(log.(D[i])) + norm((I_A[i] * F_sam[:, i]) ./ sqrt.(D[i]))^2 ) + 
               loglikelihood(Gamma(aϕ[i], bϕ[i]), [ϕ_sam[i, l]]);
            getAD(coords, NN.nnIndx, NN.nnDist, NN.nnIndxLU, ϕ_sam[i, l + 1], 0.5, A_new[i], D_new[i]);
            I_A_new[i] = sparse(nnIndx_row, nnIndx_col, vcat(-A_new[i], ones(n)));
            lh_new = -0.5 * (sum(log.(D_new[i]))  + norm((I_A_new[i] * F_sam[:, i]) ./ sqrt.(D_new[i]))^2) +
                   loglikelihood(Gamma(aϕ[i], bϕ[i]), [ϕ_sam[i, l + 1]]);     
            A_sam[l, i] = min(exp(lh_new - lh_old), 1.0);
            if rand(1)[1] < A_sam[l, i]
                I_A[i] = copy(I_A_new[i]); D[i] = copy(D_new[i]);        # update and update the corresponding I_A D
            else 
                ϕ_sam[i, l + 1] = ϕ_sam[i, l];
            end
        else 
            A_sam[l, i] = 0.0;
            ϕ_sam[:, l + 1] = ϕ_sam[:, l];   
        end
    end  

    io4 = open("../../results/BSLMC_Factor/ϕ_sam_nopredC.csv", "a" );
    writedlm(io4, ϕ_sam[:, l + 1], ", ");
    close(io4); 
    io5 = open("../../results/BSLMC_Factor/A_sam_nopredC.csv", "a" );
    writedlm(io5, A_sam[l, :], ", ");
    close(io5)
                    
                    
    # Prediction:
    if(l > N_pre_burn) 
        for j in 1:K
            getAD(coords, MnnIndx, Mnndists, MnnIndxLU, 
                 ϕ_sam[j, l + 1], 0.5, Atilde, Dtilde);
            AtildeM = sparse(repeat(1:NM, inner = m), MnnIndx, Atilde, NM, n);
            F_M_sam[:, j] = AtildeM * F_sam[:, j] + sqrt.(Dtilde) .* rand(Normal(), NM);
        end
        ω_incp_M_sam = F_M_sam * γ_sam[(p + 1):(p + K), :] + lllM * transpose(γ_sam[1, :]);
        ω_incp_M_sam_mean = ω_incp_M_sam_mean + (ω_incp_M_sam ./ N_after_burn);
        ω_incp_M_sam_var = ω_incp_M_sam_var + (ω_incp_M_sam.^2 ./ N_after_burn);
        # update Y
        Y_M_sam = X_ord[U_indx, 2:p] * γ_sam[2:p, :] + ω_incp_M_sam + 
                        transpose(rand(MvNormal(Σ_sam), NM));
        Y_M_sam_mean = Y_M_sam_mean + (Y_M_sam ./ N_after_burn);
        Y_M_sam_var = Y_M_sam_var + (Y_M_sam.^2 ./ N_after_burn); 
         
    end

    next!(prog) # monitor the progress
end
ω_incp_sam_var = (ω_incp_sam_var - ω_incp_sam_mean.^2) * (N_after_burn / (N_after_burn - 1));
for ind in 1:q
    Y_m_sam_var[ind] = (Y_m_sam_var[ind] - Y_m_sam_mean[ind].^2) * (N_after_burn / (N_after_burn - 1));
end
ω_incp_M_sam_var = (ω_incp_M_sam_var - ω_incp_M_sam_mean.^2) * (N_after_burn / (N_after_burn - 1));
Y_M_sam_var = (Y_M_sam_var - Y_M_sam_mean.^2) * (N_after_burn / (N_after_burn - 1));             

  7.090440 seconds (38.85 M allocations: 10.504 GiB, 16.75% gc time)
  2.628366 seconds (1.73 M allocations: 2.230 GiB, 30.48% gc time)
  9.695781 seconds (2.39 M allocations: 1.475 GiB)
  6.676642 seconds (36.83 M allocations: 10.526 GiB, 18.92% gc time)


Computing initial pass...  0%|                                                  |  ETA: 3 days, 13:44:04

  2.362913 seconds (167 allocations: 2.862 GiB, 33.03% gc time)
  9.362449 seconds (370 allocations: 1.314 GiB, 5.25% gc time)
 

Computing initial pass...  0%|                                                  |  ETA: 3 days, 0:40:28

 6.525943 seconds (36.29 M allocations: 10.859 GiB, 19.62% gc time)
  2.341541 seconds (167 allocations: 2.862 GiB, 33.79% gc time)
  8.726539 seconds (286 allocations: 1.104 GiB, 6.26% gc time)
 

...

Computing initial pass...100%|██████████████████████████████████████████████████|  ETA: 0:00:54

  2.211913 seconds (167 allocations: 2.862 GiB, 32.81% gc time)
 13.790859 seconds (658 allocations: 2.035 GiB, 3.00% gc time)
  5.778070 seconds (36.29 M allocations: 10.499 GiB, 16.17% gc time)


Computing initial pass...100%|██████████████████████████████████████████████████|  ETA: 0:00:27

  2.203917 seconds (167 allocations: 2.862 GiB, 32.72% gc time)
 13.842399 seconds (658 allocations: 2.035 GiB, 2.98% gc time)
  5.754810 seconds (36.29 M allocations: 10.499 GiB, 16.05% gc time)


Computing initial pass...100%|██████████████████████████████████████████████████| Time: 3 days, 3:18:40


In [21]:
RWM_scale

2-element Array{Float64,1}:
 0.16875630659969226 
 0.006267985477916082

In [22]:
@save "../../results/BSLMC_Factor/BSLMC_Factor_mean_var_nopredC.jld" ω_incp_sam_mean ω_incp_sam_var Y_m_sam_mean Y_m_sam_var ω_incp_M_sam_mean ω_incp_M_sam_var Y_M_sam_mean Y_M_sam_var 

In [23]:
@save "../../results/BSLMC_Factor/BSLMC_Factor_sum_data_nopredC.jld" Y_ord S_indx U_indx M_Sind U_ind K p q N_sam N_pre_burn NM